This notebook is a simple sanity check for the wrapper of the se3dif algorithm using simulated data.

In [1]:
from pathlib import Path

import yaml
import trimesh
import numpy as np

from se3dif.visualization import create_gripper_marker

from grasping_benchmarks.se3dif import Se3DifGraspPlanner
from grasping_benchmarks.base import CameraData
from grasping_benchmarks.base.transformations import rotation_and_position_to_homogeneous_matrix

/usr/local/lib/python3.8/dist-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
ACRONYM_DATASET_PATH = Path("/home/data/")

In [3]:
pointcloud = np.load(
    list(
        (
            Path.cwd().parent
            / "test_data"
            / "pointcloud_segmented_points"
            / "011_banana"
        ).glob("*.npy")
    )[0]
)

pointcloud.shape

(2190, 3)

In [4]:
N_POINTS = 1000
TARGET_MAX_SIZE = 0.3*8 # 0.3 is roughly the average max extent of the objects in the dataset

pointcloud = pointcloud[np.random.choice(len(pointcloud), N_POINTS)]
pointcloud_offset = np.mean(pointcloud, axis=0)
pointcloud -= pointcloud_offset

pointcloud_extents = np.max(pointcloud, axis=0) - np.min(pointcloud, axis=0)
scale_factor = TARGET_MAX_SIZE / np.max(pointcloud_extents)
pointcloud *= scale_factor

In [5]:
with open(Path.cwd().parent / "cfg" / "partial_pointcloud_config.yaml", "r") as f:
    cfg = yaml.load(f)

planner = Se3DifGraspPlanner(cfg)

/tmp/ipykernel_10718/3434412652.py:2: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  cfg = yaml.load(f)


In [6]:
camera_data = CameraData(pointcloud_segmented=pointcloud)

In [7]:
grasps = planner.plan_grasps(camera_data)

In [8]:
def visualize_grasp_axis(H_grasp, gripper_height=None):
    gripper_height = gripper_height or 0.02

    grasp_point = trimesh.primitives.Sphere(radius=0.004, center=H_grasp[:3, 3])

    # assumption: grasp axis is along z-axis of gripper coordinate system
    grasp_vector = trimesh.creation.cylinder(
        radius=0.002,
        segment=(H_grasp[:3, 3], H_grasp[:3, 3] + gripper_height * H_grasp[:3, 2]),
    )

    return trimesh.util.concatenate([grasp_point, grasp_vector])


scene = trimesh.Scene()
for point in pointcloud:
    scene.add_geometry(trimesh.primitives.Sphere(radius=0.02, center=point))

for grasp in grasps:
    H_grasp = rotation_and_position_to_homogeneous_matrix(
        grasp.rotation, grasp.position
    )
    scene.add_geometry(create_gripper_marker().apply_transform(H_grasp))
    scene.add_geometry(visualize_grasp_axis(H_grasp, 1))

scene.show()